In [1]:
from gensim.models import Word2Vec, KeyedVectors
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sn
import os
import datetime as dt
import re
import warnings
from sklearn.model_selection import train_test_split
warnings.filterwarnings('ignore')
import statsmodels.api as sm
%matplotlib inline

/usr/local/lib/python3.6/dist-packages/statsmodels/tools/_testing.py:19: FutureWarning: pandas.util.testing is deprecated. Use the functions in the public API at pandas.testing instead.
  import pandas.util.testing as tm


In [17]:
from google.colab import files
files.upload()

Saving dataset1.csv to dataset1.csv


{'dataset1.csv': b",department,no_of_trainings,avg_training_score,education,Views,date_1,date_2,date_3\n0,Sales & Marketing,1,49,Master's & above,7855.0,2005-09-10,2005-08-02,2005-08-09\n1,Operations,1,60,Bachelor's,55801.0,2005-08-18,2006-04-06,2007-11-07\n2,Sales & Marketing,1,50,Bachelor's,8067.0,2006-04-29,2006-05-12,2006-08-18\n3,Sales & Marketing,2,50,Bachelor's,27064.0,2004-02-07,2004-02-01,2004-02-18\n4,Technology,1,73,Bachelor's,13986.0,2006-02-28,2006-05-12,2006-08-18\n5,Analytics,2,85,Bachelor's,5577.0,2005-05-20,2006-04-08,2006-04-17\n6,Operations,1,59,Bachelor's,17184.0,2005-05-22,2006-11-09,2007-03-16\n7,Operations,1,63,Master's & above,312.0,2004-01-31,2006-11-09,2007-03-16\n8,Analytics,1,83,Bachelor's,53738.0,2004-01-31,2006-10-12,2006-12-18\n9,Sales & Marketing,1,54,Master's & above,227.0,2004-08-12,2005-02-19,2005-08-23\n10,Technology,1,77,Bachelor's,141836.0,2005-06-19,2004-10-01,2004-10-18\n11,Sales & Marketing,1,50,Bachelor's,8086.0,2003-10-31,2006-08-04,2006-08-09

## **Sample Dataset**

In [18]:
### data_with_datetime is the dataset where date is in datetime format, while data_without_datetime is in string or object format
data_with_datetime = pd.read_csv('dummy.csv')
data_without_datetime = pd.read_csv('dataset1.csv')

In [19]:
data_with_datetime.head()

Unnamed: 0         department  ...      date_2      date_3
0           0  Sales & Marketing  ...  2003-12-17  2004-06-11
1           1         Operations  ...  2005-08-16  2005-10-14
2           2  Sales & Marketing  ...  2005-06-19  2005-07-01
3           3  Sales & Marketing  ...  2005-06-19  2005-07-01
4           4         Technology  ...  2003-08-16  2003-08-20

[5 rows x 9 columns]

In [23]:
data_with_datetime['date_1'] = pd.to_datetime(data_with_datetime['date_1'])
data_with_datetime['date_2'] = pd.to_datetime(data_with_datetime['date_2'])
data_with_datetime['date_3'] = pd.to_datetime(data_with_datetime['date_3'])

In [24]:
data_with_datetime.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 54808 entries, 0 to 54807
Data columns (total 9 columns):
 #   Column              Non-Null Count  Dtype         
---  ------              --------------  -----         
 0   Unnamed: 0          54808 non-null  int64         
 1   department          54808 non-null  object        
 2   no_of_trainings     54808 non-null  int64         
 3   avg_training_score  54808 non-null  int64         
 4   education           54808 non-null  object        
 5   Views               54808 non-null  float64       
 6   date_1              54808 non-null  datetime64[ns]
 7   date_2              54808 non-null  datetime64[ns]
 8   date_3              54808 non-null  datetime64[ns]
dtypes: datetime64[ns](3), float64(1), int64(3), object(2)
memory usage: 3.8+ MB


In [21]:
data_without_datetime.head()

Unnamed: 0         department  ...      date_2      date_3
0           0  Sales & Marketing  ...  2005-08-02  2005-08-09
1           1         Operations  ...  2006-04-06  2007-11-07
2           2  Sales & Marketing  ...  2006-05-12  2006-08-18
3           3  Sales & Marketing  ...  2004-02-01  2004-02-18
4           4         Technology  ...  2006-05-12  2006-08-18

[5 rows x 9 columns]

In [22]:
data_without_datetime.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 54808 entries, 0 to 54807
Data columns (total 9 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Unnamed: 0          54808 non-null  int64  
 1   department          54808 non-null  object 
 2   no_of_trainings     54808 non-null  int64  
 3   avg_training_score  54808 non-null  int64  
 4   education           54808 non-null  object 
 5   Views               54808 non-null  float64
 6   date_1              54808 non-null  object 
 7   date_2              54808 non-null  object 
 8   date_3              54808 non-null  object 
dtypes: float64(1), int64(3), object(5)
memory usage: 3.8+ MB


## **Date Difference**

date_difference function first checks if date is present is datetime format, if not then it converts it into datetime, and then gathers all the date columns, and finally finds the difference between every two date columns.

In [27]:
def date_difference(dataframe):
    
    data = dataframe.copy()
### checking if date is present in datetime format        
    date_present = False
    is_date = []
    for col in data.columns:
        if data[col].dtypes=='datetime64[ns]':
            is_date.append(True)
        else:
            is_date.append(False)
        
    if True in is_date:
        date_present = True
    else:
        date_present = False

### if date is not present in datetime format, finding the columns that can be converted to datetime        
### case 1: when datetime is not present    
    if date_present == False:
        to_date = []
        for col in data.columns:
            try:
                if data[col].dtypes=='object':
                    if pd.to_datetime(data[col]).dtypes == 'datetime64[ns]':
                        to_date.append(col)
            except Exception as e:
                pass
        
        for date_col in to_date:
            data[date_col] = pd.to_datetime(data[date_col])
            
### Calculating the difference between dates                        
    dates = []
    for col in data.columns:
        if data[col].dtypes == 'datetime64[ns]':
            dates.append(col)
    
    while dates:
        if len(dates)>1:
            col_first = dates[0]
            for col_next in dates[1:]:
                data['days_diff'+'_'+col_first+'_'+col_next] = np.abs(data[col_first] - data[col_next])
        dates = dates[1:]
        
    return data    

In [28]:
date_difference(data_with_datetime)

Unnamed: 0  ... days_diff_date_2_date_3
0               0  ...                177 days
1               1  ...                 59 days
2               2  ...                 12 days
3               3  ...                 12 days
4               4  ...                  4 days
...           ...  ...                     ...
54803       54803  ...                  4 days
54804       54804  ...                185 days
54805       54805  ...                  5 days
54806       54806  ...                  4 days
54807       54807  ...                 17 days

[54808 rows x 12 columns]

In [29]:
date_difference(data_without_datetime)

Unnamed: 0  ... days_diff_date_2_date_3
0               0  ...                  7 days
1               1  ...                580 days
2               2  ...                 98 days
3               3  ...                 17 days
4               4  ...                 98 days
...           ...  ...                     ...
54803       54803  ...                  8 days
54804       54804  ...                 17 days
54805       54805  ...                 37 days
54806       54806  ...                189 days
54807       54807  ...                771 days

[54808 rows x 12 columns]

## **Outliers Analysis**

The following function takes votes from 3 different outlier detection functions, and if at least 2 of them confirm that a data point is an outlier, it replaces the value at that index with the Median of the variable. 

In [36]:
dataset = data_with_datetime.iloc[:,1:]

In [34]:
def outliers(dataframe):
    
    data = dataframe.copy()
    
    is_continuous = []
    for col in data.columns:
        if (data[col].dtypes == 'int32') or (data[col].dtypes == 'int64') or (data[col].dtypes == 'float64'):
            col_len = len(data[col].unique())
            if col_len>40:
                is_continuous.append(col)
    
### Percentile based detection of outliers, where an interval is set, and if a data point is found outside the interval it is considered an outlier
    def percentile_based(data, threshold = 95):
        diff = (100 - threshold)/2
        minval, maxval = np.percentile(data, [diff, 100-diff])
        return ((data<minval) | (data>maxval))

### Median based detection, where a psuedo z-score is calculated using the median, and a threshold is set. If the calculated psuedo z-score is beyond the threshold it is considered an outlier
    def median_based(data, threshold=3.5):
        median = np.median(data)
        mad = np.median([np.abs(y - median) for y in data])
        modified_zscore = [(0.6745*(y - median)/mad) for y in data]
        return np.abs(modified_zscore)>threshold

### Using z-score for detection, where a threshold of 3 is set if the absolute z-score of a data point is beyond 3, it is considered an outlier
    def std_div(data, threshold=3):
        std = data.std()
        mean = data.mean()
        isOutlier = []
        for val in data:
            if np.abs(val-mean)/std > threshold:
                isOutlier.append(True)
            else:
                isOutlier.append(False)
        return np.array(isOutlier)

### Outliers votes are taken, if any two if the above functions confirm that a data point is an outlier, it is considered an outlier
    def outliervote(data):
        x = percentile_based(data)
        y = median_based(data)
        z = std_div(data)

        temp = zip(data.index, x, y, z)
        temp = list(temp)
        final = []

        for i in range(len(temp)):
            if temp[i].count(False) >= 2:
                final.append(False)
            else:
                final.append(True)

        return np.array(final)

### Replacing outliers with the median of the column    
    for col in is_continuous:
        out_df = pd.DataFrame(outliervote(data[col]), columns = ['outlier'])
        out_idx = list(out_df[out_df.outlier==True].index)
        without_idx = list(out_df[out_df.outlier==False].index)
        data_out = data.iloc[out_idx,:]
        data_without = data.iloc[without_idx,:]
        
        median = data[col].median()
        data_out[col] = median
        
        data = pd.concat([data_out, data_without])
                                
    return data                            

In [37]:
outliers(dataset)

department  no_of_trainings  ...     date_2     date_3
95             Analytics                1  ... 2004-01-04 2004-01-09
100           Operations                1  ... 2005-08-16 2005-10-14
110    Sales & Marketing                3  ... 2005-06-13 2005-07-22
155           Operations                1  ... 2005-06-19 2005-07-01
176          Procurement                3  ... 2004-01-04 2004-01-09
...                  ...              ...  ...        ...        ...
54803         Technology                1  ... 2003-08-16 2003-08-20
54804         Operations                1  ... 2005-02-19 2005-08-23
54805          Analytics                1  ... 2004-09-09 2004-09-14
54806  Sales & Marketing                1  ... 2005-09-15 2005-09-19
54807                 HR                1  ... 2004-10-01 2004-10-18

[54808 rows x 8 columns]

## **Removing columns with Peasrson correlation > 0.85**

Pearson correlation is the correlation between two **Quantitative** or **Continuous** variables. Hence, first find the continuous variables and then remove columns with correlation > 0.85

In [40]:
def overly_correlated(data):
    
### Find the continuous variables in the dataset    
    is_continuous = []
    for col in data.columns:
        if (data[col].dtypes == 'int32') or (data[col].dtypes == 'int64') or (data[col].dtypes == 'float64'):
            col_len = len(data[col].unique())
            if col_len>40:
                is_continuous.append(col)
    
### Find the columns whose Pearson correlation is more than 0.85    
    corr = data[is_continuous].corr()    
    cols_drop = []
    corr_cols = corr.columns
    for col in corr_cols:
        if len(corr[col][corr[col]>0.85])>1:
            cols_drop.append(col)
            
    return data.drop(cols_drop, axis=1)     

In [41]:
overly_correlated(dataset)

department  no_of_trainings  ...     date_2     date_3
0      Sales & Marketing                1  ... 2003-12-17 2004-06-11
1             Operations                1  ... 2005-08-16 2005-10-14
2      Sales & Marketing                1  ... 2005-06-19 2005-07-01
3      Sales & Marketing                2  ... 2005-06-19 2005-07-01
4             Technology                1  ... 2003-08-16 2003-08-20
...                  ...              ...  ...        ...        ...
54803         Technology                1  ... 2003-08-16 2003-08-20
54804         Operations                1  ... 2005-02-19 2005-08-23
54805          Analytics                1  ... 2004-09-09 2004-09-14
54806  Sales & Marketing                1  ... 2005-09-15 2005-09-19
54807                 HR                1  ... 2004-10-01 2004-10-18

[54808 rows x 8 columns]